In [3]:
from src.RawDataLoaders import CodeSearchNet_RawDataLoader, CoNaLa_RawDataLoader, Django_RawDataLoader

import openai
import random
import json
from tqdm.auto import tqdm 
openai.api_key = "sk-sxT83HQHcYWya4CThZOPfRyDm9hZggqSpEvmJfTh"

%load_ext autoreload
%autoreload 2
%load_ext line_profiler

# A simple exampe using GPT-3 for question answering

In [4]:
prompt = '''Paragraph 1: It is well evidenced that repeated exposure to an idea increases the chance that an individual will ‘adopt’ that idea. 
This is why advertisers show adverts over and over, and why YouTube repeatedly serves up the same suggested videos. 
The algorithms have identified that the more individuals see something, the more attractive or trustworthy it appears. 
Similarly, the more that we hear an idea directly from other people, the more it is ‘socially reinforced’ as being good or accurate.'''.replace('Student', 'Step')

response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=30, temperature=0, logprobs=100, stop='Finished', echo=True)
print(response['choices'][0]['text'])

Paragraph 1: It is well evidenced that repeated exposure to an idea increases the chance that an individual will ‘adopt’ that idea. 
This is why advertisers show adverts over and over, and why YouTube repeatedly serves up the same suggested videos. 
The algorithms have identified that the more individuals see something, the more attractive or trustworthy it appears. 
Similarly, the more that we hear an idea directly from other people, the more it is ‘socially reinforced’ as being good or accurate. 
This is why we are more likely to believe something if it is told to us by a friend or family member, rather than a stranger.


In [742]:
response.to_dict()

{'id': 'cmpl-4i5OCAaYGYYFLiafXTTkB1j4',
 'object': 'text_completion',
 'created': 1601302612,
 'model': 'davinci:2020-05-03',
 'choices': [<OpenAIObject at 0x7f2dbed20d58> JSON: {
    "finish_reason": "length",
    "index": 0,
    "logprobs": {
      "text_offset": [
        0,
        3,
        9,
        11,
        12,
        15,
        18,
        23,
        33,
        38,
        47,
        56,
        59,
        62,
        67,
        77,
        81,
        88,
        93,
        96,
        107,
        112,
        112,
        114,
        116,
        119,
        119,
        120,
        125,
        130,
        131,
        132,
        133,
        137,
        140,
        144,
        156,
        161,
        164,
        169,
        174,
        178,
        183,
        184,
        188,
        192,
        200,
        211,
        218,
        221,
        225,
        230,
        240,
        247,
        248,
        249,
        250,
        253,
 

In [467]:
d

{'id': 'cmpl-xcBWUDxoawrRUfRMnC81z3Rd',
 'object': 'text_completion',
 'created': 1600934465,
 'model': 'davinci:2020-05-03',
 'choices': [<OpenAIObject at 0x7f30e4331f68> JSON: {
    "finish_reason": "length",
    "index": 0,
    "logprobs": {
      "text_offset": [
        194,
        200,
        207,
        208,
        216,
        217,
        222,
        225,
        229,
        237,
        243,
        246,
        250,
        257,
        264,
        267,
        272,
        277,
        278,
        279
      ],
      "token_logprobs": [
        -0.12964875,
        -0.002114281,
        -0.13852057,
        -0.258049,
        -0.0011484785,
        -0.8933736,
        -0.7957046,
        -0.031762272,
        -1.3572965,
        -0.75108737,
        -0.26355308,
        -0.0367888,
        -0.042848423,
        -0.0026872677,
        -0.14905174,
        -0.30263224,
        -0.0019407182,
        -0.007019224,
        -0.01547479,
        -0.0054665143
      ],
    

## Testing it with code from CoNaLa

In [16]:
conala_RawDataLoader = CoNaLa_RawDataLoader()

In [79]:
conala_RawDataLoader.get_samples('test')[10]

{'description': 'sending http headers to `client`',
 'code': "client.send('HTTP/1.0 200 OK\\r\\n')"}

In [152]:
setup_prompt = "These are descriptions with python code from StackOverflow\n\n"
num_examples = 30
train_samples = conala_RawDataLoader.get_samples('train')
random.shuffle(train_samples)
for sample_obj in train_samples[0:num_examples]:
    setup_prompt += f"description: {sample_obj['description']}\n"
    setup_prompt += f"code: {sample_obj['code']}\n"
    setup_prompt += '\n'

# sample_obj = conala_RawDataLoader.get_samples('test')[5]
# # setup_prompt += f"code: {sample_obj['code']}\n"
# setup_prompt += "code: client.send('HTTP/1.0 200 OK\\r\\n')\n"
# setup_prompt += f"descripion:"
# print(setup_prompt)
# print()
# # print(f"Ground truth: {sample_obj['description']}")

In [156]:
print(setup_prompt)

These are descriptions with python code from StackOverflow

description: import a module 'a.b.c' with importlib.import_module in python 2
code: importlib.import_module('a.b.c')

description: Exclude column names when writing dataframe `df` to a csv file `filename.csv`
code: df.to_csv('filename.csv', header=False)

description: sort column `m` in panda dataframe `df`
code: df.sort('m')

description: Selenium `driver` click a hyperlink with the pattern "a[href^='javascript']"
code: driver.find_element_by_css_selector("a[href^='javascript']").click()

description: match regex pattern 'TAA(?:[ATGC]{3})+?TAA' on string `seq`
code: re.findall('TAA(?:[ATGC]{3})+?TAA', seq)

description: multiply all items in a list `[1, 2, 3, 4, 5, 6]` together
code: from functools import reduce
reduce(lambda x, y: x * y, [1, 2, 3, 4, 5, 6])

description: create list `done` containing permutations of each element in list `[a, b, c, d]` with variable `x` as tuples
code: done = [(el, x) for el in [a, b, c, d]]


In [154]:
test_samples = conala_RawDataLoader.get_samples('test')

In [155]:
for sample_obj in tqdm(test_samples):
    prompt = setup_prompt
    prompt += f"descripion: {sample_obj['description']}\n"
    prompt += f"code:"
    response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=100, temperature=0, stop='\n')
    desc = sample_obj['description']
    pred_code = response['choices'][0]['text'].strip()
    true_code = sample_obj['code']
    sample_obj['GPT3_pred_code'] = pred_code
    print(f'Desc: {desc}')
    print(f'True: {true_code}')
    print(f'Pred: {pred_code}')
    print()
json.dump(test_samples, open("GPT3_CoNaLa_predictions.json", 'w'), indent=4)

Desc: send a signal `signal.SIGUSR1` to the current process
True: os.kill(os.getpid(), signal.SIGUSR1)
Pred: os.kill(os.getpid(), signal.SIGUSR1)

Desc: decode a hex string '4a4b4c' to UTF-8.
True: bytes.fromhex('4a4b4c').decode('utf-8')
Pred: '4a4b4c'.decode('utf-8')

Desc: check if all elements in list `myList` are identical
True: all(x == myList[0] for x in myList)
Pred: myList == [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

Desc: format number of spaces between strings `Python`, `:` and `Very Good` to be `20`
True: print('%*s : %*s' % (20, 'Python', 20, 'Very Good'))
Pred: 'Python : Very Good'.format(' ' * 20)

Desc: How to convert a string from CP-1251 to UTF-8?
True: d.decode('cp1251').encode('utf8')
Pred: unicode(string, 'cp1251').encode('utf-8')

Desc: get rid of None values in dictionary `kwargs`
True: res = {k: v for k, v in list(kwargs.items()) if v is not None}
Pred: kwargs.pop('key', None)

Desc: get rid of None values in dictionary `kwargs`
True: res = dict((k, v) for k, v in kwargs.

### Evaluating on BLEU

In [196]:
from src.Experiments import Sequence_BLEU_Experiment

In [218]:
samples = json.load(open('saved_models/TranX/CoNaLa_TranX_predictions.json'))

In [219]:
samples[0]

{'description': 'send a signal `signal.SIGUSR1` to the current process',
 'code': 'os.kill(os.getpid(), signal.SIGUSR1)',
 'pred_code': "os.system('<unk> <unk> <unk>')",
 'BLEU': 0.0,
 'unsmoothed_official_BLEU': 0.0,
 'nltk_BLEU': 0.05816635421147516}

In [220]:
samples = Sequence_BLEU_Experiment(fields = {'predicted_seq':'pred_code', 'target_seq':'code'})(samples)

unsmoothed_official_BLEU: 0.22539098849201342
nltk_BLEU: 0.2529552430370321


In [227]:
for sample in samples:
    print(f"{sample['nltk_BLEU']:.5f}")

0.05817
0.32776
0.12911
0.04180
0.47386
0.05972
0.02065
0.01170
0.85657
0.04652
0.02238
0.06315
0.25164
0.78399
0.46945
0.18319
0.18493
0.59460
0.12468
0.10894
0.01764
0.33872
0.35706
0.11202
1.00000
0.72725
1.00000
0.00002
0.56395
0.23357
0.04881
0.29580
0.06824
0.02389
0.09238
0.12549
0.86334
0.24346
0.06230
0.28489
0.04864
0.12107
0.00828
0.07530
0.23334
0.37238
0.08475
0.52186
0.30266
0.76354
0.30951
0.47648
0.59755
0.11732
0.19194
0.05422
0.29312
0.26760
0.05447
0.09980
0.08095
0.37981
0.00403
0.50763
0.08517
0.13292
0.04457
0.13182
0.42375
0.27825
0.05810
0.06883
0.15628
0.30604
0.04108
0.22422
0.19871
0.13169
0.14406
0.39680
0.11306
0.04518
0.02457
0.26883
0.72490
0.38815
0.08134
0.02459
0.05108
0.02497
0.02432
0.02653
0.11499
0.93733
0.33573
0.63241
0.65918
0.51872
0.18789
0.41033
0.03418
0.06863
0.06863
0.35631
0.42611
0.19697
0.14488
0.16923
0.19741
0.03899
0.28527
0.01601
0.23263
0.01355
0.13984
0.07536
0.27855
0.29176
0.11154
0.05064
0.08472
0.04065
0.05300
0.08295
0.13267


# Running GPT3 on the Django dataset

In [160]:
django_RawDataLoader = Django_RawDataLoader()

In [162]:
len(django_RawDataLoader.get_samples('test'))

1881

In [165]:
setup_prompt = "These are descriptions with python code\n\n"
num_examples = 20
train_samples = django_RawDataLoader.get_samples('train')
random.shuffle(train_samples)
for sample_obj in train_samples[0:num_examples]:
    setup_prompt += f"description: {sample_obj['description']}\n"
    setup_prompt += f"code: {sample_obj['code']}\n"
    setup_prompt += '\n'

In [487]:
print(setup_prompt)

These are python snippets from StackOverflow with their descriptions

code: soup.findAll(attrs={'name': 'description'})
description: BeautifulSoup find all tags with attribute 'name' equal to 'description'

code: urllib.parse.unquote(url).decode('utf8')
description: decode url `url` from UTF-16 code to UTF-8 code

code: [list(v) for k, v in itertools.groupby(mylist, key=lambda x: x[:5])]
description: split list `mylist` into a list of lists whose elements have the same first five characters

code: sorted(matrix, key=itemgetter(1))
description: sort 2d array `matrix` by row with index 1

code: writer.writerows(A)
description: Write all tuple of tuples `A` at once into csv file

code: os.system('screencapture screen.png')
description: take screenshot 'screen.png' on mac os x

code: datetime.datetime.strptime('2011, 4, 0', '%Y, %U, %w')
description: derive the week start for the given week number and year ‘2011, 4, 0’

code: datetime.datetime.now().strftime('%a')
description: obtain the c

In [167]:
test_samples = django_RawDataLoader.get_samples('test')

In [168]:
for sample_obj in tqdm(test_samples):
    prompt = setup_prompt
    prompt += f"descripion: {sample_obj['description']}\n"
    prompt += f"code:"
    response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=100, temperature=0, stop='\n')
    desc = sample_obj['description']
    pred_code = response['choices'][0]['text'].strip()
    true_code = sample_obj['code']
    sample_obj['GPT3_pred_code'] = pred_code
    print(f'Desc: {desc}')
    print(f'True: {true_code}')
    print(f'Pred: {pred_code}')
    print()
json.dump(test_samples, open("GPT3_django_predictions.json", 'w'), indent=4)

Desc: from threading import local into default name space.
True: from threading import local
Pred: from threading import local

Desc: import module warnings.
True: import warnings
Pred: import warnings

Desc: from django.conf import settings into default name space.
True: from django . conf import settings
Pred: from django . conf import settings

Desc: from django.core import signals into default name space.
True: from django . core import signals
Pred: from django . core import signals

Desc: from django.core.cache.backends.base import InvalidCacheBackendError, CacheKeyWarning and BaseCache into default name space.
True: from django . core . cache . backends . base import (  InvalidCacheBackendError , CacheKeyWarning , BaseCache )
Pred: from django . core . cache . backends . base import InvalidCacheBackendError , CacheKeyWarning , BaseCache

Desc: from django.core.exceptions import ImproperlyConfigured into default name space.
True: from django . core . exceptions import ImproperlyC

# Looking at GPT3's tokenisation
is it the same as GPT2's?

In [182]:
from transformers import BartTokenizer
tokenizer = BartTokenizer.from_pretrained("facebook/bart-large")

In [183]:
tokenizer("\n\u00a0")['input_ids']

[0, 2]

### Evaluating on BLEU

In [186]:
from src.Experiments import Sequence_BLEU_Experiment

In [191]:
samples = json.load(open('saved_models/GPT_3/GPT3_django_test_predictions.json'))

In [192]:
samples = Sequence_BLEU_Experiment(fields = {'predicted_seq':'GPT3_pred_code', 'target_seq':'code'})(samples)

unsmoothed_official_BLEU: 0.5958150351684434
nltk_BLEU: 0.8097363933329027


In [190]:
samples[:100]

[{'description': 'send a signal `signal.SIGUSR1` to the current process',
  'code': 'os.kill(os.getpid(), signal.SIGUSR1)',
  'GPT3_pred_code': 'os.kill(os.getpid(), signal.SIGUSR1)',
  'unsmoothed_official_BLEU': 0.0,
  'nltk_BLEU': 1.0},
 {'description': "decode a hex string '4a4b4c' to UTF-8.",
  'code': "bytes.fromhex('4a4b4c').decode('utf-8')",
  'GPT3_pred_code': "'4a4b4c'.decode('utf-8')",
  'unsmoothed_official_BLEU': 0.0,
  'nltk_BLEU': 0.550104853348733},
 {'description': 'check if all elements in list `myList` are identical',
  'code': 'all(x == myList[0] for x in myList)',
  'GPT3_pred_code': 'myList == [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]',
  'unsmoothed_official_BLEU': 0.0,
  'nltk_BLEU': 0.04714627368490467},
 {'description': 'format number of spaces between strings `Python`, `:` and `Very Good` to be `20`',
  'code': "print('%*s : %*s' % (20, 'Python', 20, 'Very Good'))",
  'GPT3_pred_code': "'Python : Very Good'.format(' ' * 20)",
  'unsmoothed_official_BLEU': 0.0,
  'nltk_

# Annotating the mined CoNaLa samples

In [234]:
import jsonlines

In [407]:
conala_RawDataLoader = CoNaLa_RawDataLoader()

In [425]:
setup_prompt = "These are python snippets from StackOverflow with their descriptions\n\n"
num_examples = 20
train_samples = conala_RawDataLoader.get_samples('train')
random.shuffle(train_samples)
for sample_obj in train_samples[0:num_examples]:
    setup_prompt += f"code: {sample_obj['code']}\n"
    setup_prompt += f"description: {sample_obj['description']}\n"
    setup_prompt += '\n'

In [426]:
print(setup_prompt)

These are python snippets from StackOverflow with their descriptions

code: soup.findAll(attrs={'name': 'description'})
description: BeautifulSoup find all tags with attribute 'name' equal to 'description'

code: urllib.parse.unquote(url).decode('utf8')
description: decode url `url` from UTF-16 code to UTF-8 code

code: [list(v) for k, v in itertools.groupby(mylist, key=lambda x: x[:5])]
description: split list `mylist` into a list of lists whose elements have the same first five characters

code: sorted(matrix, key=itemgetter(1))
description: sort 2d array `matrix` by row with index 1

code: writer.writerows(A)
description: Write all tuple of tuples `A` at once into csv file

code: os.system('screencapture screen.png')
description: take screenshot 'screen.png' on mac os x

code: datetime.datetime.strptime('2011, 4, 0', '%Y, %U, %w')
description: derive the week start for the given week number and year ‘2011, 4, 0’

code: datetime.datetime.now().strftime('%a')
description: obtain the c

In [248]:
test_samples = []
with jsonlines.open('datasets/CoNaLa/conala-corpus/conala-mined.jsonl') as reader:
    for sample_obj in reader:
        test_samples.append({'code':sample_obj['snippet'], 'original_desc':sample_obj['intent']})

In [417]:
test_samples = conala_RawDataLoader.get_samples('valid')

In [413]:
test_samples[0]

{'description': "Concatenate elements of a list 'x' of multiple integers to a single integer",
 'code': 'sum(d * 10 ** i for i, d in enumerate(x[::-1]))'}

In [252]:
test_samples[0]

{'code': 'sorted(l, key=lambda x: (-int(x[1]), x[0]))',
 'original_desc': 'Sort a nested list by two elements',
 'GPT3_pred_desc': 'sort a list of lists `l` by the second item in each list'}

In [253]:
json.dump(test_samples, open("GPT3_CoNaLa_mined_desc_predictions.json", 'w'), indent=4)

In [ ]:
for sample_obj in tqdm(test_samples):
    prompt = setup_prompt
    prompt += f"code: {sample_obj['code']}\n"
    prompt += f"description:"
    response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=100, temperature=0, stop='\n')
    pred_desc = response['choices'][0]['text'].strip()
    original_desc = sample_obj['code']
    sample_obj['GPT3_pred_desc'] = pred_desc
    print(f'Code: {sample_obj["code"]}')
    print(f'Orig: {original_desc}')
    print(f'Pred: {pred_desc}')
    print()
json.dump(test_samples, open("GPT3_CoNaLa_mined_desc_predictions.json", 'w'), indent=4)

Code: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Orig: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Pred: sort a list of lists `l` by the second item in each list

Code: [int(x) for x in str(num)]
Orig: [int(x) for x in str(num)]
Pred: convert string `str` to an integer `int`

Code: c.decode('unicode_escape')
Orig: c.decode('unicode_escape')
Pred: decode a string `c` from `unicode_escape` encoding

Code: parser.add_argument('-t', dest='table', help='', nargs='+')
Orig: parser.add_argument('-t', dest='table', help='', nargs='+')
Pred: add a new argument `-t` to parser

Code: datetime.datetime.strptime(s, '%Y-%m-%dT%H:%M:%SZ')
Orig: datetime.datetime.strptime(s, '%Y-%m-%dT%H:%M:%SZ')
Pred: parse a string `s` to a datetime object `datetime.datetime`

Code: np.array(x._data).reshape(x.size[::-1]).T
Orig: np.array(x._data).reshape(x.size[::-1]).T
Pred: transpose a numpy array `x`

Code: soup.get_text().replace('\n', '\n\n')
Orig: soup.get_text().replace('\n', '\n\n')
Pred: replace newline c

#### In parallel

In [403]:
@ray.remote(num_cpus=0.3)
def call_API(sample_obj, setup_prompt):
    prompt = setup_prompt
    prompt += f"code: {sample_obj['code']}\n"
    prompt += f"description:"
    openai.api_key = "sk-sxT83HQHcYWya4CThZOPfRyDm9hZggqSpEvmJfTh"
    response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=100, temperature=0, stop='\n')
    pred_desc = response['choices'][0]['text'].strip()
    sample_obj['GPT3_pred_desc'] = pred_desc
    return sample_obj

In [418]:
new_chunked_GPT3_test = []

In [419]:
for chunk_samples in tqdm(list(chunks(test_samples,500))):
    GPT3_test_samples_500 = ray.get([call_API.remote(sample_obj, setup_prompt) for sample_obj in chunk_samples if len(sample_obj['code'])<1500])
    new_chunked_GPT3_test += GPT3_test_samples_500

In [420]:
json.dump(new_chunked_GPT3_test, open("GPT3_description_CoNaLa_valid.json", 'w'), indent=4)

# Using ray to call the GPT3 API in parallel

In [324]:
from src.useful_utils import chunks

In [255]:
import ray
ray.init(ignore_reinit_error=True)

2020-09-24 09:04:09,191	INFO resource_spec.py:231 -- Starting Ray with 21.83 GiB memory available for workers and up to 10.91 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-09-24 09:04:09,838	INFO services.py:1193 -- View the Ray dashboard at localhost:8265
2020-09-24 09:04:09,841	WARNING services.py:1567 -- WARNING: The object store is using /tmp instead of /dev/shm because /dev/shm has only 67100672 bytes available. This may slow down performance! You may be able to free up space by deleting files in /dev/shm or terminating any running plasma_store_server processes. If you are inside a Docker container, you may need to pass an argument with the flag '--shm-size' to 'docker run'.
2020-09-24 09:04:09,884	WARNING services.py:1567 -- WARNING: The object store is using /tmp instead of /dev/shm because /dev/shm has only 67100672 bytes available. This may slow down performance! You may be able to free up space by deleting file

{'node_ip_address': '10.130.2.171',
 'raylet_ip_address': '10.130.2.171',
 'redis_address': '10.130.2.171:6379',
 'object_store_address': '/tmp/ray/session_2020-09-24_09-04-09_190205_127108/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2020-09-24_09-04-09_190205_127108/sockets/raylet',
 'webui_url': 'localhost:8265',
 'session_dir': '/tmp/ray/session_2020-09-24_09-04-09_190205_127108'}

2020-09-24 09:04:11,322	WARNING worker.py:1134 -- The dashboard on node pythonmlnotebookgpu2-1-hn8b8 failed with the following error:
Traceback (most recent call last):
  File "/usr/lib/python3.6/asyncio/base_events.py", line 1062, in create_server
    sock.bind(sa)
OSError: [Errno 99] Cannot assign requested address

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.6/dist-packages/ray/dashboard/dashboard.py", line 961, in <module>
    dashboard.run()
  File "/usr/local/lib/python3.6/dist-packages/ray/dashboard/dashboard.py", line 576, in run
    aiohttp.web.run_app(self.app, host=self.host, port=self.port)
  File "/usr/local/lib/python3.6/dist-packages/aiohttp/web.py", line 433, in run_app
    reuse_port=reuse_port))
  File "/usr/lib/python3.6/asyncio/base_events.py", line 484, in run_until_complete
    return future.result()
  File "/usr/local/lib/python3.6/dist-packages/aiohttp/web.py", line 359, i

In [427]:
mined_samples = []
with jsonlines.open('datasets/CoNaLa/conala-corpus/conala-mined.jsonl') as reader:
    for sample_obj in reader:
        mined_samples.append({'code':sample_obj['snippet'], 'original_desc':sample_obj['intent']})
        
mining_dict = set()
filtered_mined_samples = []
for sample_obj in mined_samples:
    if sample_obj['code'] not in mining_dict:
        filtered_mined_samples.append(sample_obj)
        mining_dict.add(sample_obj['code'])

#### Analysing the mined samples

In [292]:
mined_code = [s['code'] for s in filtered_mined_samples[:77382]]

In [428]:
len([c['code'] for c in filtered_mined_samples if len(c['code']) < 1000])

499167

In [313]:
for i, s in enumerate(filtered_mined_samples):
    if s['code'] == 'l[0][0] += 1':
        print(i)
        break

18140


#### Callign the API

In [490]:
@ray.remote(num_cpus=0.3)
def call_API(sample_obj, setup_prompt):
    prompt = setup_prompt
    prompt += f"code: {sample_obj['code']}\n"
    prompt += f"description:"
    openai.api_key = "sk-sxT83HQHcYWya4CThZOPfRyDm9hZggqSpEvmJfTh"
    response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=100, temperature=0.6, stop='\n', logprobs=100)
    pred_desc = response['choices'][0]['text'].strip()
    sample_obj['GPT3_pred_desc'] = pred_desc
    sample_obj['GPT3_top_100_logprobs'] = response.to_dict()
    return sample_obj

In [502]:
new_chunked_GPT3_mined = []

In [ ]:
for chunk_samples in tqdm(list(chunks(filtered_mined_samples[377370:],50))):
    GPT3_mined_samples_500 = ray.get([call_API.remote(sample_obj, setup_prompt) for sample_obj in chunk_samples if len(sample_obj['code'])<800])
    new_chunked_GPT3_mined += GPT3_mined_samples_500

In [499]:
293214+84155

377369

In [504]:
len(new_chunked_GPT3_mined)

121867

In [340]:
new_chunked_GPT3_mined[2]

{'code': 'ax.set_title(title)',
 'original_desc': 'Change the title of factor plot in seaborn',
 'GPT3_pred_desc': 'set the title of a matplotlib plot `ax`'}

In [277]:
GPT3_mined_samples = json.load(open('saved_models/GPT_3/GPT3_CoNaLa_mined_desc_predictions_0_to_20635_pred.json'))

In [278]:
GPT3_mined_samples[0]

{'code': 'sorted(l, key=lambda x: (-int(x[1]), x[0]))',
 'original_desc': 'Sort a nested list by two elements',
 'GPT3_pred_desc': 'sort a list of lists `l` by the second item in each list'}

In [259]:
for i, s in enumerate(GPT3_mined_samples):
    if 'GPT3_pred_desc' not in s:
        print(i)
        break

20635


In [274]:
temp_mined_samples = mined_samples[:]

In [505]:
GPT3_solid_state_mined += new_chunked_GPT3_mined

In [506]:
len(GPT3_solid_state_mined)

501784

In [286]:
GPT3_solid_state_mined[20734]['GPT3_pred_desc'] = 'add one to the first nested element of list `l`'

In [507]:
json.dump(GPT3_solid_state_mined, open("GPT3_CoNaLa_mined_solid_state_501784.json", 'w'), indent=4)

In [501]:
GPT3_solid_state_mined[-1]

{'code': 'self.last_link = None',
 'original_desc': 'Using Regex to Search for HTML links near keywords',
 'GPT3_pred_desc': 'set the last link of a chain to None',
 'GPT3_top_100_logprobs': {'id': 'cmpl-yL05YKxzDIOpHdBiVYTQtFNC',
  'object': 'text_completion',
  'created': 1601080013,
  'model': 'davinci:2020-05-03',
  'choices': [<OpenAIObject at 0x7f25228cdfc0> JSON: {
     "finish_reason": "stop",
     "index": 0,
     "logprobs": {
       "text_offset": [
         2589,
         2593,
         2597,
         2602,
         2607,
         2610,
         2612,
         2618,
         2621,
         2626,
         2626,
         2626,
         2626,
         2626,
         2626
       ],
       "token_logprobs": [
         -0.98790395,
         -0.85882217,
         -0.3778364,
         -0.23400594,
         -0.661487,
         -0.6466564,
         -1.5581853,
         -0.92186534,
         -0.38491082,
         -0.26092693,
         -0.029848408,
         -0.06341417,
         -0.00

In [511]:
GPT3_solid_state_mined_no_probs = []
for s in GPT3_solid_state_mined:
    GPT3_solid_state_mined_no_probs.append({
        'code':s['code'],
        'original_desc':s['original_desc'],
        'GPT3_pred_desc':s['GPT3_pred_desc']
    })

In [512]:
json.dump(GPT3_solid_state_mined_no_probs, open("GPT3_CoNaLa_mined_solid_state_501784_no_probs.json", 'w'), indent=4)

# Creating a conversational dataset with GPT3

In [702]:
setup_prompt = '''The following is a conversation between a student programmer and a senior programmer. They are both aiming to create the implementation named: Target. The student programmer asks for the high level descriptions to create the program in steps. The senior advises the student of the high level goals for each step. Building the desired implementations takes only 3 to 10 steps.

Target: new_list = [(x*2) for x in my_list]
Step 1: new_list = []
Step 2: new_list = [x for x in my_list]
Step 3: new_list = [(x*2) for x in my_list]
Senior: I want to multiply all elements in a list by two. Can you start with the simplest case?
Senior: Create an empty list.
Step 1: new_list = []
Senior: Great! How about we iterate over the elements of a list called `my_list` 
Step 2: new_list = [x for x in my_list]
Senior: Can you multiply each element x by two now.
Step 3: new_list = [(x*2) for x in my_list]
Senior: Excellent!

Target: parser.add_argument('-t', dest='table', help='', nargs='+')
Step 1: parser.add_argument()
Step 2: parser.add_argument('-t')
Step 3: parser.add_argument('-t', dest='table')
Step 4: parser.add_argument('-t', dest='table', help='')
Step 5: parser.add_argument('-t', dest='table', help='', nargs='+')
Senior: I would like to add parameters to a line argument parser. Can you start with the simplest case? 
Senior: Add an empty argument.
Step 1: parser.add_argument()
Senior: Make `t` the first parameter.
Step 2: parser.add_argument('-t')
Senior: Set the descination to `table`.
Step 3: parser.add_argument('-t', dest='table')
Senior: Could you add an empty help string?
Step 4: parser.add_argument('-t', dest='table', help='')
Senior: Set the number of args to more than 1.
Step 5: parser.add_argument('-t', dest='table', help='', nargs='+')
Senior: Excellent!

Target: df.to_csv('your_example_filename.csv', header=False)
Step 1: df.to_csv()
Step 2: df.to_csv('your_example_filename.csv')
Step 3: df.to_csv('your_example_filename.csv', header=False)
Senior: I would like to save a pandas dataframe `df` to a csv file. Can you start with the simplest case?
Senior: Call `to_csv` on df.
Step 1: df.to_csv()
Senior: Pass `filename.csv` to it as a string.
Step 2: df.to_csv('your_example_filename.csv')
Senior: And make sure we ignore headers.
Step 3: df.to_csv('your_example_filename.csv', header=False)
Senior: Excellent!

Target: [int(s) for s in example_string.split(',')]
Step 1: [s for s in example_string]
Step 2: [int(s) for s in example_string]
Step 3: [int(s) for s in example_string.split()]
Step 4: [int(s) for s in example_string.split(',')]
Senior: I would like to split a string into a list of integers. Can you start with the simplest case?
Senior: Make a list comprehension.
Step 1: [s for s in example_string]
Senior: Cast each element to an int.
Step 2: [int(s) for s in example_string]
Senior: Split the string.
Step 3: [int(s) for s in example_string.split()]
Senior: Split the string by `,`.
Step 4: [int(s) for s in example_string.split(',')]
Senior: Excellent!

Target: print(' '.join(sorted(my_list, key=lambda k: len(k), reverse=True)))
Step 1: print(my_list)
Step 2: print(sorted(my_list, reverse=True))
Step 3: print(''.join(sorted(my_list, reverse=True)))
Step 4: print(' '.join(sorted(my_list, reverse=True)))
Step 5: print(' '.join(sorted(my_list, key=lambda k: len(k), reverse=True)))
Senior: I would like to print the sorted elements of a list `my_list` in reverse order by length as a string. Can you start with the simplest case?
Senior: Print a list.
Step 1: print(my_list)
Senior: Can you sort the list in descending order?
Step 2: print(sorted(my_list, reverse=True))
Senior: Now convert the sorted list to a string with the join function
Step 3: print(''.join(sorted(my_list, reverse=True)))
Senior: Add a space between each element.
Step 4: print(' '.join(sorted(my_list, reverse=True)))
Senior: Sort the list by the length of its elements.
Step 5: print(' '.join(sorted(my_list, key=lambda k: len(k), reverse=True)))
Senior: Excellent!

Target: sorted(l, key=lambda x: -int(x[1]))
Step 1: sorted(l)
Step 2: sorted(l, key=lambda x: x)
Step 3: sorted(l, key=lambda x: x[1])
Step 4: sorted(l, key=lambda x: int(x[1]))
Step 5: sorted(l, key=lambda x: -int(x[1]))
Senior: Let's sort a nested list `l` in reverse by the second element. Can you start with the simplest case?
Senior: Sort a list.
Step 1: sorted(l)
Senior: Now add a custom key function.
Step 2: sorted(l, key=lambda x: x)
Senior: Perfect, access the second element of `x` in the lambda.
Step 3: sorted(l, key=lambda x: x[1])
Senior: Cast it to an integer.
Step 4: sorted(l, key=lambda x: int(x[1]))
Senior: Make it descending.
Step 5: sorted(l, key=lambda x: -int(x[1]))
Senior: Excellent!

'''

In [703]:
mined_samples = []
with jsonlines.open('datasets/CoNaLa/conala-corpus/conala-mined.jsonl') as reader:
    for sample_obj in reader:
        mined_samples.append({'code':sample_obj['snippet'], 'original_desc':sample_obj['intent']})
        
mining_dict = set()
filtered_mined_samples = []
for sample_obj in mined_samples:
    if sample_obj['code'] not in mining_dict:
        filtered_mined_samples.append(sample_obj)
        mining_dict.add(sample_obj['code'])

In [682]:
train_samples = conala_RawDataLoader.get_samples('train')

In [683]:
train_samples[0]

{'description': "Concatenate elements of a list 'x' of multiple integers to a single integer",
 'code': 'sum(d * 10 ** i for i, d in enumerate(x[::-1]))'}

In [743]:
@ray.remote(num_cpus=0.3)
def call_API(sample_obj, setup_prompt):
    prompt = setup_prompt
    prompt += f"Target: {sample_obj['code']}"
    openai.api_key = "sk-sxT83HQHcYWya4CThZOPfRyDm9hZggqSpEvmJfTh"
    response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=300, temperature=0, stop='Target')
    pred_desc = response['choices'][0]['text']
    sample_obj['GPT3_pred_conv'] = f"Target: {sample_obj['code']}" + pred_desc
#     sample_obj['GPT3_top_100_logprobs'] = response.to_dict()
    return sample_obj

In [721]:
GPT3_conv_solid_state = []

In [744]:
new_chunked_GPT3_mined = []

In [745]:
for chunk_samples in tqdm(list(chunks(filtered_mined_samples[22241:],1))):
    GPT3_mined_samples_500 = ray.get([call_API.remote(sample_obj, setup_prompt) for sample_obj in chunk_samples if len(sample_obj['code'])<150])
    new_chunked_GPT3_mined += GPT3_mined_samples_500

KeyboardInterrupt: 

In [722]:
GPT3_conv_solid_state += new_chunked_GPT3_mined

In [723]:
json.dump(GPT3_conv_solid_state, open("GPT3_CoNaLa_conv_mined_v1.3_22240.json", 'w'), indent=4)

In [719]:
len(new_chunked_GPT3_mined)

22240

In [709]:
len("""datetime.datetime.strptime('2013-1-25', '%Y-%m-%d').strftime('%m/%d/%y')""")

72

In [724]:
for s in new_chunked_GPT3_mined:
    print(s['GPT3_pred_conv'])
    print()

Target: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Step 1: sorted(l)
Step 2: sorted(l, key=lambda x: x)
Step 3: sorted(l, key=lambda x: x[1])
Step 4: sorted(l, key=lambda x: int(x[1]))
Step 5: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Senior: Let's sort a nested list `l` in reverse by the second element. Can you start with the simplest case?
Senior: Sort a list.
Step 1: sorted(l)
Senior: Now add a custom key function.
Step 2: sorted(l, key=lambda x: x)
Senior: Perfect, access the second element of `x` in the lambda.
Step 3: sorted(l, key=lambda x: x[1])
Senior: Cast it to an integer.
Step 4: sorted(l, key=lambda x: int(x[1]))
Senior: Make it descending.
Step 5: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Senior: Excellent!



Target: [int(x) for x in str(num)]
Step 1: [int(x) for x in str(num)]
Senior: I would like to convert a string to an integer. Can you start with the simplest case?
Senior: Convert the string to a list of integers.
Step 1: [int(x) for x in str(num)]
Senior: Cast

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [648]:
GPT3_conv_samples = json.load(open('GPT3_CoNaLa_conv_mined_v1.3.json'))
for s in GPT3_conv_samples:
    print(s['GPT3_pred_conv'])
    print()

Target: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Step 1: sorted(l)
Step 2: sorted(l, key=lambda x: x)
Step 3: sorted(l, key=lambda x: x[1])
Step 4: sorted(l, key=lambda x: int(x[1]))
Step 5: sorted(l, key=lambda x: -int(x[1]))
Step 6: sorted(l, key=lambda x: (-int(x[1]), x[0]))
Senior: Let's sort a nested list `l` in reverse by the second element. Can you start with the simplest case?
Senior: Sort a list.
Step 1: sorted(l)
Senior: Now add a custom key function.
Step 2: sorted(l, key=lambda x: x)
Senior: Perfect, access the second element of `x` in the lambda.
Step 3: sorted(l, key=lambda x: x[1])
Senior: Cast it to an integer.
Step 4: sorted(l, key=lambda x: int(x[1]))
Senior: Make it descending.
Step 5: sorted(l, key=lambda x: -int(x[1]))
Senior: Can you return the first element of `x` and the index?
Step 6: sorted(l, key=lambda x: (-int(x[1

Target: [int(x) for x in str(num)]
Step 1: [int(x) for x in str(num)]
Step 2: [int(x) for x in str(num).split(',')]
Senior: I would like to e

# GPT3 on CAsT

In [5]:
from src.RawDataLoaders import CAsT_RawDataLoader
CAsT_raw_data_loader = CAsT_RawDataLoader()
get_query_fn = CAsT_raw_data_loader.get_query
get_doc_fn = CAsT_raw_data_loader.get_doc
CAsT_q_rels = CAsT_raw_data_loader.q_rels

In [9]:
samples = CAsT_raw_data_loader.get_topics('train')

In [65]:
cast_2020_topics = json.load(open('datasets/TREC_CAsT/treccastweb/2020/2020_manual_evaluation_topics_v1.0.json'))

In [25]:
samples[24]

{'prev_turns': ['33_1', '33_2', '33_3', '33_4', '33_5', '33_6', '33_7'],
 'q_id': '33_8',
 'q_rel': ['CAR_b9348816e6e63881858b3f42704e04204e4e5611']}

In [40]:
None+1

TypeError: unsupported operand type(s) for +: 'NoneType' and 'int'

In [56]:
setup_prompt = 'The following is a sequence of queries for a search engine.\n"Query" indicates the previous resolved queries.\n"Raw" indicates the unresolved version that needs to be fixed.\n\n'
for topic in [samples[8],samples[19],samples[24]]:
    setup_prompt += 'Conversation:\n'
    last_idx = -1
    for i, q_id in enumerate(topic['prev_turns']):
        q_raw_text = get_query_fn(q_id, utterance_type="raw_utterance")
        q_manual_text = get_query_fn(q_id, utterance_type="manual_rewritten_utterance")
        setup_prompt += f"Raw: {q_raw_text}\n"
        setup_prompt += f"Fixed: {q_manual_text}\n"
        setup_prompt += '\n'
        last_idx = i
    setup_prompt += f"Raw: {get_query_fn(topic['q_id'], utterance_type='raw_utterance')}\n"
    setup_prompt += f"Fixed: {get_query_fn(topic['q_id'], utterance_type='manual_rewritten_utterance')}\n"
    setup_prompt += "\n"
print(setup_prompt)

The following is a sequence of queries for a search engine.
"Query" indicates the previous resolved queries.
"Raw" indicates the unresolved version that needs to be fixed.

Conversation:
Raw: What is throat cancer?
Fixed: What is throat cancer?

Raw: Is it treatable?
Fixed: Is throat cancer treatable?

Raw: Tell me about lung cancer.
Fixed: Tell me about lung cancer.

Raw: What are its symptoms? 
Fixed: What are lung cancer's symptoms?

Raw: Can it spread to the throat?
Fixed: Can lung cancer spread to the throat?

Raw: What causes throat cancer?
Fixed: What causes throat cancer?

Raw: What is the first sign of it?
Fixed: What is the first sign of throat cancer?

Raw: Is it the same as esophageal cancer?
Fixed: Is throat cancer the same as esophageal cancer?

Raw: What's the difference in their symptoms?
Fixed: What's the difference in throat cancer and esophageal cancer's symptoms?

Conversation:
Raw: What are the different types of sharks?
Fixed: What are the different types of shark

In [70]:
setup_prompt = '''The following is a sequence of queries for a search engine. The task involves rewriting the last query such that it contains all relevant information from previous queries.

Conversation:
Previous: What is throat cancer?
Last: Is it treatable?
Last rewritten: Is throat cancer treatable?

Conversation:
Previous: What is throat cancer?
Previous: Is throat cancer treatable?
Previous: Tell me about lung cancer.
Last: What are its symptoms? 
Last rewritten: What are lung cancer's symptoms?

Conversation:
Previous: Tell me about the Neverending Story film.
Previous: What is the Neverending Story film about?
Previous: Who was the author and when was the Neverending Story film published?
Last: What are it's main themes?
Fixed: What are the main themes of the Neverending Story film?

Conversation:
Previous: What are the benefits of the new Apple iPad?
Last: I want to buy one. Where?
Last rewritten: Where can I buy the new Apple iPad?

Conversation:
Previous: What are the benefits of the new Apple iPad?
Previous: How does the Apple iPad compare to the Dell XPS lineup?
Previous: Are Dell laptops impact resistant?
Last: Do they have a durarability rating?
Last rewritten: Do Dell laptops have a durarability rating?

Conversation:
Previous: What are the differences between skateboards and longboards?
Previous: Why does skateboard truck width affect stability?
Previous: Is Baker a good brand for skateboard trucks?
Previous: What benefit do spacers have when setting up a skateboard?
Previous: Do professional skateboarders use spacers?
Previous: What kinds of woods are used to make longboards?
Previous: Is maple more flexible than plywood?
Last: Tell me if they can be heat treated?
Last rewritten: Can maple and plywood be heat treated?

'''

In [84]:
for topic in tqdm(cast_2020_topics):
    for i in range(len(topic['turn'])):
        prompt = setup_prompt
        prompt += 'Conversation:\n'
        prev_turns = topic['turn'][:i]
        turn = topic['turn'][i]
        last_idx = -1
        for j, t in enumerate(prev_turns):
#             prompt += f"Raw: {t['raw_utterance']}\n"
            prompt += f"Previous:{t['GPT3_rewritten_utterance']}\n"
            last_idx = j
        
        prompt += f"Last: {turn['raw_utterance']}\n"
        prompt += f"Last rewritten:"
        response = openai.Completion.create(engine="davinci", prompt=prompt, max_tokens=300, temperature=0.4, stop='\n')
        pred_desc = response['choices'][0]['text']
        turn['GPT3_rewritten_utterance_temp_0.4'] = pred_desc


In [85]:
json.dump(cast_2020_topics, open("saved_models/GPT_3/GPT3_CAsT_2020.json", 'w'), indent=4)

In [83]:
cast_2020_topics[1]

{'number': 82,
 'turn': [{'number': 1,
   'raw_utterance': 'I would like to learn about GMO Food labeling.',
   'manual_rewritten_utterance': 'I would like to learn about GMO Food labeling.',
   'automatic_rewritten_utterance': 'I would like to learn about GMO Food labeling.',
   'manual_canonical_result_id': 'MARCO_955185',
   'GPT3_rewritten_utterance': ' Tell me about GMO food labeling.',
   'GPT3_rewritten_utterance_temp_0.8': ' Tell me about GMO food labeling.',
   'GPT3_rewritten_utterance_temp_1.0': ' Tell me about GMO food labeling?'},
  {'number': 2,
   'raw_utterance': 'What are the pros and cons?',
   'manual_rewritten_utterance': 'What are the pros and cons of GMO food labeling?',
   'automatic_rewritten_utterance': 'What are the pros and cons of GMO Food labeling?',
   'manual_canonical_result_id': 'CAR_bafb3c1c72e23c444e182cac4e0ea9e4330d21c9',
   'GPT3_rewritten_utterance': ' What are the pros and cons of GMO food labeling?',
   'GPT3_rewritten_utterance_temp_0.8': ' Wha